# Masakhane - Machine Translation for African Languages (Using JoeyNMT)

## Note before beginning:
### - The idea is that you should be able to make minimal changes to this in order to get SOME result for your own translation corpus. 

### - The tl;dr: Go to the **"TODO"** comments which will tell you what to update to get up and running

### - If you actually want to have a clue what you're doing, read the text and peek at the links

### - With 100 epochs, it should take around 7 hours to run in Google Colab

### - Once you've gotten a result for your language, please attach and email your notebook that generated it to masakhanetranslation@gmail.com

### - If you care enough and get a chance, doing a brief background on your language would be amazing. See examples in  [(Martinus, 2019)](https://arxiv.org/abs/1906.05685)

## Retrieve your data & make a parallel corpus

If you are wanting to use the JW300 data referenced on the Masakhane website or in our GitHub repo, you can use `opus-tools` to convert the data into a convenient format. `opus_read` from that package provides a convenient tool for reading the native aligned XML files and to convert them to TMX format. The tool can also be used to fetch relevant files from OPUS on the fly and to filter the data as necessary. [Read the documentation](https://pypi.org/project/opustools-pkg/) for more details.

Once you have your corpus files in TMX format (an xml structure which will include the sentences in your target language and your source language in a single file), we recommend reading them into a pandas dataframe. Thankfully, Jade wrote a silly `tmx2dataframe` package which converts your tmx file to a pandas dataframe. 

In [0]:
"""from google.colab import drive
drive.mount('/content/drive')"""

In [1]:
# TODO: Set your source and target languages. Keep in mind, these traditionally use language codes as found here:
# These will also become the suffix's of all vocab and corpus files used throughout
import os
source_language = "en"
target_language = "tiv" 
lc = False  # If True, lowercase the data.
seed = 42  # Random seed for shuffling.
tag = "jw300-baseline" # Give a unique name to your folder - this is to ensure you don't rewrite any models you've already submitted

os.environ["src"] = source_language # Sets them in bash as well, since we often use bash scripts
os.environ["tgt"] = target_language
os.environ["tag"] = tag


# This will save it to a folder in our gdrive instead!
!mkdir -p "en_tiv/$src-$tgt-$tag"
os.environ["experiment_path"] = "en_tiv/%s-%s-%s" % (source_language, target_language, tag)

In [2]:
!mkdir -p "en_tiv/$src-$tgt-$tag"

In [3]:
!echo $experiment_path

en_tiv/en-tiv-jw300-baseline


In [4]:
# Install opus-tools
! pip install opustools-pkg

You are using pip version 10.0.1, however version 20.0.2 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.


In [5]:
# Downloading our corpus
! opus_read -d JW300 -s $src -t $tgt -wm moses -w jw300.$src jw300.$tgt -q

# extract the corpus file
! gunzip JW300_latest_xml_$src-$tgt.xml.gz


Alignment file /proj/nlpl/data/OPUS/JW300/latest/xml/en-tiv.xml.gz not found. The following files are available for downloading:

   2 MB https://object.pouta.csc.fi/OPUS-JW300/v1/xml/en-tiv.xml.gz
 263 MB https://object.pouta.csc.fi/OPUS-JW300/v1/xml/en.zip
  25 MB https://object.pouta.csc.fi/OPUS-JW300/v1/xml/tiv.zip

 290 MB Total size
./JW300_latest_xml_en-tiv.xml.gz ... 100% of 2 MB
./JW300_latest_xml_en.zip ... 100% of 263 MB
./JW300_latest_xml_tiv.zip ... 100% of 25 MB


In [6]:
# Download the global test set.
! wget https://raw.githubusercontent.com/juliakreutzer/masakhane/master/jw300_utils/test/test.en-any.en
  
# And the specific test set for this language pair.
os.environ["trg"] = target_language 
os.environ["src"] = source_language 

! wget https://raw.githubusercontent.com/juliakreutzer/masakhane/master/jw300_utils/test/test.en-$trg.en 
! mv test.en-$trg.en test.en
! wget https://raw.githubusercontent.com/juliakreutzer/masakhane/master/jw300_utils/test/test.en-$trg.$trg 
! mv test.en-$trg.$trg test.$trg

--2020-02-12 15:17:58--  https://raw.githubusercontent.com/juliakreutzer/masakhane/master/jw300_utils/test/test.en-any.en
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 199.232.24.133
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|199.232.24.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 277791 (271K) [text/plain]
Saving to: ‘test.en-any.en’

test.en-any.en      100%[===================>] 271.28K  --.-KB/s    in 0.01s   

2020-02-12 15:17:58 (26.3 MB/s) - ‘test.en-any.en’ saved [277791/277791]

--2020-02-12 15:17:58--  https://raw.githubusercontent.com/juliakreutzer/masakhane/master/jw300_utils/test/test.en-tiv.en
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 199.232.24.133
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|199.232.24.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 26584 (26K) [text/plain]
Saving to: ‘test.en-tiv.en’

test.en-tiv.e

In [7]:
# Read the test data to filter from train and dev splits.
# Store english portion in set for quick filtering checks.
en_test_sents = set()
filter_test_sents = "test.en-any.en"
j = 0
with open(filter_test_sents) as f:
  for line in f:
    en_test_sents.add(line.strip())
    j += 1
print('Loaded {} global test sentences to filter from the training/dev data.'.format(j))

Loaded 3571 global test sentences to filter from the training/dev data.


In [8]:
import pandas as pd

# TMX file to dataframe
source_file = 'jw300.' + source_language
target_file = 'jw300.' + target_language

source = []
target = []
skip_lines = []  # Collect the line numbers of the source portion to skip the same lines for the target portion.
with open(source_file) as f:
    for i, line in enumerate(f):
        # Skip sentences that are contained in the test set.
        if line.strip() not in en_test_sents:
            source.append(line.strip())
        else:
            skip_lines.append(i)             
with open(target_file) as f:
    for j, line in enumerate(f):
        # Only add to corpus if corresponding source was not skipped.
        if j not in skip_lines:
            target.append(line.strip())
    
print('Loaded data and skipped {}/{} lines since contained in test set.'.format(len(skip_lines), i))
    
df = pd.DataFrame(zip(source, target), columns=['source_sentence', 'target_sentence'])
# if you get TypeError: data argument can't be an iterator is because of your zip version run this below
#df = pd.DataFrame(list(zip(source, target)), columns=['source_sentence', 'target_sentence'])
df.head(3)

Loaded data and skipped 2535/209778 lines since contained in test set.


source_sentence  \
0                             Questions From Readers   
1  How seriously should Christians view an engage...   
2  An engagement to marry is a cause for happines...   

                                     target_sentence  
0          Mbampin Mba Mbaôron Takerada Ne Ve Pin la  
1  Gba u ityendezwa i nomsoor vea kwase ve er u v...  
2  Ityendezwa i̱ nomsoor vea kwase ve er ér vea v...

## Pre-processing and export

It is generally a good idea to remove duplicate translations and conflicting translations from the corpus. In practice, these public corpora include some number of these that need to be cleaned.

In addition we will split our data into dev/test/train and export to the filesystem.

In [9]:
# drop duplicate translations
df_pp = df.drop_duplicates()

# drop conflicting translations
# (this is optional and something that you might want to comment out 
# depending on the size of your corpus)
df_pp.drop_duplicates(subset='source_sentence', inplace=True)
df_pp.drop_duplicates(subset='target_sentence', inplace=True)

# Shuffle the data to remove bias in dev set selection.
df_pp = df_pp.sample(frac=1, random_state=seed).reset_index(drop=True)

/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/ipykernel/__main__.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/ipykernel/__main__.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


In [10]:
# Install fuzzy wuzzy to remove "almost duplicate" sentences in the
# test and training sets.
! pip install fuzzywuzzy
! pip install python-Levenshtein
import time
from fuzzywuzzy import process
import numpy as np
from os import cpu_count
from functools import partial
from multiprocessing import Pool


# reset the index of the training set after previous filtering
df_pp.reset_index(drop=False, inplace=True)

# Remove samples from the training data set if they "almost overlap" with the
# samples in the test set.

# Filtering function. Adjust pad to narrow down the candidate matches to
# within a certain length of characters of the given sample.
def fuzzfilter(sample, candidates, pad):
  candidates = [x for x in candidates if len(x) <= len(sample)+pad and len(x) >= len(sample)-pad] 
  if len(candidates) > 0:
    return process.extractOne(sample, candidates)[1]
  else:
    return np.nan

You are using pip version 10.0.1, however version 20.0.2 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.
You are using pip version 10.0.1, however version 20.0.2 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.


In [11]:
start_time = time.time()
### iterating over pandas dataframe rows is not recomended, let use multi processing to apply the function

with Pool(cpu_count()-1) as pool:
    scores = pool.map(partial(fuzzfilter, candidates=list(en_test_sents), pad=5), df_pp['source_sentence'])
hours, rem = divmod(time.time() - start_time, 3600)
minutes, seconds = divmod(rem, 60)
print("done in {}h:{}min:{}seconds".format(hours, minutes, seconds))

# Filter out "almost overlapping samples"
df_pp = df_pp.assign(scores=scores)
df_pp = df_pp[df_pp['scores'] < 95]

done in 0.0h:18.0min:34.256463050842285seconds


In [12]:
# This section does the split between train/dev for the parallel corpora then saves them as separate files
# We use 1000 dev test and the given test set.
import csv

# Do the split between dev/train and create parallel corpora
num_dev_patterns = 1000

# Optional: lower case the corpora - this will make it easier to generalize, but without proper casing.
if lc:  # Julia: making lowercasing optional
    df_pp["source_sentence"] = df_pp["source_sentence"].str.lower()
    df_pp["target_sentence"] = df_pp["target_sentence"].str.lower()

# Julia: test sets are already generated
dev = df_pp.tail(num_dev_patterns) # Herman: Error in original
stripped = df_pp.drop(df_pp.tail(num_dev_patterns).index)

with open("train."+source_language, "w") as src_file, open("train."+target_language, "w") as trg_file:
  for index, row in stripped.iterrows():
    src_file.write(row["source_sentence"]+"\n")
    trg_file.write(row["target_sentence"]+"\n")
    
with open("dev."+source_language, "w") as src_file, open("dev."+target_language, "w") as trg_file:
  for index, row in dev.iterrows():
    src_file.write(row["source_sentence"]+"\n")
    trg_file.write(row["target_sentence"]+"\n")

#stripped[["source_sentence"]].to_csv("train."+source_language, header=False, index=False)  # Herman: Added `header=False` everywhere
#stripped[["target_sentence"]].to_csv("train."+target_language, header=False, index=False)  # Julia: Problematic handling of quotation marks.

#dev[["source_sentence"]].to_csv("dev."+source_language, header=False, index=False)
#dev[["target_sentence"]].to_csv("dev."+target_language, header=False, index=False)

# Doublecheck the format below. There should be no extra quotation marks or weird characters.
! head train.*
! head dev.*

==> train.en <==
How we say something can be as important as what we say .
All of them in wisdom you have made . The earth is full of your productions . ”
The surviving righteous ones will see that God’s prophetic word is true .
Take a lesson from the lilies of the field , how they are growing ; they do not toil , nor do they spin ; but I say to you that not even Solomon in all his glory was arrayed as one of these . ” ​ — Matthew 6 : 28 , 29 .
Now that some time has elapsed since that change was introduced , we can ask ourselves : ‘ Am I using the time made available to have a Family Worship evening or to engage in personal study ?
What adjustments did one young couple make , and with what results ?
Such promises are practical because they enable those who put faith in them to face the future with hope and confidence . ​ — Hebrews 11 : 6 .
A step toward good study habits is regularly to set aside time for Bible study .
For some weeks , the prophet Elijah has been a guest of the widow 



---


## Installation of JoeyNMT

JoeyNMT is a simple, minimalist NMT package which is useful for learning and teaching. Check out the documentation for JoeyNMT [here](https://joeynmt.readthedocs.io)  

In [13]:
# Install JoeyNMT
! git clone https://github.com/joeynmt/joeynmt.git
! cd joeynmt; pip3 install .

fatal: destination path 'joeynmt' already exists and is not an empty directory.
Processing /home/ec2-user/SageMaker/masakhane/joeynmt
    100% |████████████████████████████████| 753.4MB 64kB/s  eta 0:00:01    21% |██████▊                         | 158.7MB 57.5MB/s eta 0:00:11    33% |██████████▊                     | 253.7MB 46.6MB/s eta 0:00:11    99% |███████████████████████████████▊| 745.9MB 56.9MB/s eta 0:00:01
    100% |████████████████████████████████| 421.8MB 116kB/s eta 0:00:01    47% |███████████████▏                | 200.2MB 60.7MB/s eta 0:00:04
    100% |████████████████████████████████| 81kB 34.4MB/s ta 0:00:01
    100% |████████████████████████████████| 225kB 38.4MB/s ta 0:00:01
    100% |████████████████████████████████| 276kB 36.0MB/s ta 0:00:01��█████████████████████▋      | 215kB 63.2MB/s eta 0:00:01
    100% |████████████████████████████████| 61kB 18.0MB/s ta 0:00:01
    100% |████████████████████████████████| 71kB 32.0MB/s ta 0:00:01
    100% |███████████████████████

    100% |████████████████████████████████| 307kB 40.9MB/s ta 0:00:01
    100% |████████████████████████████████| 92kB 37.9MB/s ta 0:00:01
    100% |████████████████████████████████| 81kB 35.4MB/s ta 0:00:01
    100% |████████████████████████████████| 2.9MB 15.6MB/s ta 0:00:01
    100% |████████████████████████████████| 163kB 42.0MB/s ta 0:00:01
    100% |████████████████████████████████| 153kB 41.2MB/s ta 0:00:01
  Stored in directory: /tmp/pip-ephem-wheel-cache-g8wwbcp9/wheels/3a/30/44/d8a7e4bf0ed7c54548bf491738b185ef57222ad3bcdfb1afc4
  Stored in directory: /home/ec2-user/.cache/pip/wheels/e4/76/4d/a95b8dd7b452b69e8ed4f68b69e1b55e12c9c9624dd962b191
  Stored in directory: /home/ec2-user/.cache/pip/wheels/2c/b1/94/43d03e130b929aae7ba3f8d15cbd7bc0d1cb5bb38a5c721833
  Stored in directory: /home/ec2-user/.cache/pip/wheels/7c/06/54/bc84598ba1daf8f970247f550b175aaaee85f68b4b0c5ab2c6
  Stored in directory: /home/ec2-user/.cache/pip/wheels/5c/2e/7e/a1d4d4fcebe6c381f378ce7743a3ced3699feb89bcf

# Preprocessing the Data into Subword BPE Tokens

- One of the most powerful improvements for agglutinative languages (a feature of most Bantu languages) is using BPE tokenization [ (Sennrich, 2015) ](https://arxiv.org/abs/1508.07909).

- It was also shown that by optimizing the umber of BPE codes we significantly improve results for low-resourced languages [(Sennrich, 2019)](https://www.aclweb.org/anthology/P19-1021) [(Martinus, 2019)](https://arxiv.org/abs/1906.05685)

- Below we have the scripts for doing BPE tokenization of our data. We use 4000 tokens as recommended by [(Sennrich, 2019)](https://www.aclweb.org/anthology/P19-1021). You do not need to change anything. Simply running the below will be suitable. 

In [14]:
!sudo pip3 install subword-nmt

You are using pip version 19.0.2, however version 20.0.2 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.


In [16]:
# One of the huge boosts in NMT performance was to use a different method of tokenizing. 
# Usually, NMT would tokenize by words. However, using a method called BPE gave amazing boosts to performance

# Do subword NMT
from os import path
os.environ["src"] = source_language # Sets them in bash as well, since we often use bash scripts
os.environ["tgt"] = target_language

# Learn BPEs on the training data.
os.environ["data_path"] = path.join("joeynmt", "data", source_language + target_language) # Herman! 
! subword-nmt learn-joint-bpe-and-vocab --input train.$src train.$tgt -s 4000 -o bpe.codes.4000 --write-vocabulary vocab.$src vocab.$tgt

# Apply BPE splits to the development and test data.
! subword-nmt apply-bpe -c bpe.codes.4000 --vocabulary vocab.$src < train.$src > train.bpe.$src
! subword-nmt apply-bpe -c bpe.codes.4000 --vocabulary vocab.$tgt < train.$tgt > train.bpe.$tgt

! subword-nmt apply-bpe -c bpe.codes.4000 --vocabulary vocab.$src < dev.$src > dev.bpe.$src
! subword-nmt apply-bpe -c bpe.codes.4000 --vocabulary vocab.$tgt < dev.$tgt > dev.bpe.$tgt
! subword-nmt apply-bpe -c bpe.codes.4000 --vocabulary vocab.$src < test.$src > test.bpe.$src
! subword-nmt apply-bpe -c bpe.codes.4000 --vocabulary vocab.$tgt < test.$tgt > test.bpe.$tgt

# Create directory, move everyone we care about to the correct location
! mkdir -p $data_path
! cp train.* $data_path
! cp test.* $data_path
! cp dev.* $data_path
! cp bpe.codes.4000 $data_path
! ls $data_path

# Also move everything we care about to a mounted location in google drive (relevant if running in colab) at gdrive_path
! cp train.* "$experiment_path"
! cp test.* "$experiment_path"
! cp dev.* "$experiment_path"
! cp bpe.codes.4000 "$gexperiment_path"
! ls "$experiment_path"

# Create that vocab using build_vocab
! sudo chmod 777 joeynmt/scripts/build_vocab.py
! joeynmt/scripts/build_vocab.py joeynmt/data/$src$tgt/train.bpe.$src joeynmt/data/$src$tgt/train.bpe.$tgt --output_path joeynmt/data/$src$tgt/vocab.txt

# Some output
! echo "BPE Tiv Sentences"
! tail -n 5 test.bpe.$tgt
! echo "Combined BPE Vocab"
! tail -n 10 joeynmt/data/$src$tgt/vocab.txt  # Herman

bpe.codes.4000	dev.en	     test.bpe.tiv    test.tiv	    train.en
dev.bpe.en	dev.tiv      test.en	     train.bpe.en   train.tiv
dev.bpe.tiv	test.bpe.en  test.en-any.en  train.bpe.tiv
cp: cannot create regular file ‘’: No such file or directory
dev.bpe.en   dev.tiv	   test.en	   train.bpe.en   train.tiv
dev.bpe.tiv  test.bpe.en   test.en-any.en  train.bpe.tiv
dev.en	     test.bpe.tiv  test.tiv	   train.en
BPE Tiv Sentences
Er nan ve yange gba u H@@ u@@ sh@@ ai una lu a ishimataver keng ve una fatyô u civir Aôndo sha mimi ?
Er nan ve i gbe u se lu a ishimataver ve se fatyô u civir Aôndo sha mimi ?
M sôn Yehova mer a wasem me taver ishima me er kwagh u m tsough u eren la .
Hegen ve gema inja , nahan ka m z@@ aan ve inya hanma shighe . ” — Ôr Anzaakaa 29 : 25 .
[ 1 ] ( ikyum@@ hi@@ ange i sha 7 ) I gema ati agen .
Combined BPE Vocab
erus@@
isholi@@
š@@
epher@@
ị
î@@
Ó@@
ö
_
ateu


# Creating the JoeyNMT Config

JoeyNMT requires a yaml config. We provide a template below. We've also set a number of defaults with it, that you may play with!

- We used Transformer architecture 
- We set our dropout to reasonably high: 0.3 (recommended in  [(Sennrich, 2019)](https://www.aclweb.org/anthology/P19-1021))

Things worth playing with:
- The batch size (also recommended to change for low-resourced languages)
- The number of epochs (we've set it at 30 just so it runs in about an hour, for testing purposes)
- The decoder options (beam_size, alpha)
- Evaluation metrics (BLEU versus Crhf4)

In [18]:
# This creates the config file for our JoeyNMT system. It might seem overwhelming so we've provided a couple of useful parameters you'll need to update
# (You can of course play with all the parameters if you'd like!)

name = '%s%s' % (source_language, target_language)
gdrive_path = os.environ["experiment_path"]

# Create the config
config = """
name: "{name}_transformer"

data:
    src: "{source_language}"
    trg: "{target_language}"
    train: "data/{name}/train.bpe"
    dev:   "data/{name}/dev.bpe"
    test:  "data/{name}/test.bpe"
    level: "bpe"
    lowercase: False
    max_sent_length: 100
    src_vocab: "data/{name}/vocab.txt"
    trg_vocab: "data/{name}/vocab.txt"

testing:
    beam_size: 5
    alpha: 1.0

training:
    #load_model: "{experiment_path}/models/{name}_transformer/1.ckpt" # if uncommented, load a pre-trained model from this checkpoint
    random_seed: 42
    optimizer: "adam"
    normalization: "tokens"
    adam_betas: [0.9, 0.999] 
    scheduling: "plateau"           # TODO: try switching from plateau to Noam scheduling
    patience: 5                     # For plateau: decrease learning rate by decrease_factor if validation score has not improved for this many validation rounds.
    learning_rate_factor: 0.5       # factor for Noam scheduler (used with Transformer)
    learning_rate_warmup: 1000      # warmup steps for Noam scheduler (used with Transformer)
    decrease_factor: 0.7
    loss: "crossentropy"
    learning_rate: 0.0003
    learning_rate_min: 0.00000001
    weight_decay: 0.0
    label_smoothing: 0.1
    batch_size: 4096
    batch_type: "token"
    eval_batch_size: 3600
    eval_batch_type: "token"
    batch_multiplier: 1
    early_stopping_metric: "ppl"
    epochs: 150                     # TODO: Decrease for when playing around and checking of working. Around 30 is sufficient to check if its working at all
    validation_freq: 1000          # TODO: Set to at least once per epoch.
    logging_freq: 100
    eval_metric: "bleu"
    model_dir: "models/{name}_transformer"
    overwrite: True               # TODO: Set to True if you want to overwrite possibly existing models. 
    shuffle: True
    use_cuda: True
    max_output_length: 100
    print_valid_sents: [0, 1, 2, 3]
    keep_last_ckpts: 5

model:
    initializer: "xavier"
    bias_initializer: "zeros"
    init_gain: 1.0
    embed_initializer: "xavier"
    embed_init_gain: 1.0
    tied_embeddings: True
    tied_softmax: True
    encoder:
        type: "transformer"
        num_layers: 6
        num_heads: 4             # TODO: Increase to 8 for larger data.
        embeddings:
            embedding_dim: 256   # TODO: Increase to 512 for larger data.
            scale: True
            dropout: 0.2
        # typically ff_size = 4 x hidden_size
        hidden_size: 256         # TODO: Increase to 512 for larger data.
        ff_size: 1024            # TODO: Increase to 2048 for larger data.
        dropout: 0.3
    decoder:
        type: "transformer"
        num_layers: 6
        num_heads: 4              # TODO: Increase to 8 for larger data.
        embeddings:
            embedding_dim: 256    # TODO: Increase to 512 for larger data.
            scale: True
            dropout: 0.2
        # typically ff_size = 4 x hidden_size
        hidden_size: 256         # TODO: Increase to 512 for larger data.
        ff_size: 1024            # TODO: Increase to 2048 for larger data.
        dropout: 0.3
""".format(name=name, experiment_path=os.environ["experiment_path"], source_language=source_language, target_language=target_language)
with open("joeynmt/configs/transformer_{name}.yaml".format(name=name),'w') as f:
    f.write(config)

In [19]:
!conda install pytorch torchvision cudatoolkit=10.1 -c pytorch --yes
!conda install tensorboard --yes
!conda install -c pytorch torchtext --yes
!conda install -c powerai sentencepiece --yes
!conda install -c powerai sacrebleu --yes

Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.5.12
  latest version: 4.8.2

Please update conda by running

    $ conda update -n base -c defaults conda



## Package Plan ##

  environment location: /home/ec2-user/anaconda3/envs/python3

  added / updated specs: 
    - cudatoolkit=10.1
    - pytorch
    - torchvision


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    certifi-2019.11.28         |           py36_0         156 KB
    ca-certificates-2020.1.1   |                0         132 KB
    openssl-1.0.2u             |       h7b6447c_0         3.1 MB
    pytorch-1.4.0              |py3.6_cuda10.1.243_cudnn7.6.3_0       432.9 MB  pytorch
    torchvision-0.5.0          |       py36_cu101         9.1 MB  pytorch
    ------------------------------------------------------------
                                           Total:       445

sentencepiece-0.1.84 | 3.1 MB    | ##################################### | 100% 
tensorflow-base-2.0. | 100.9 MB  | ##################################### | 100% 
termcolor-1.1.0      | 7 KB      | ##################################### | 100% 
_tflow_select-2.3.0  | 2 KB      | ##################################### | 100% 
google-pasta-0.1.8   | 43 KB     | ##################################### | 100% 
keras-preprocessing- | 36 KB     | ##################################### | 100% 
tensorflow-estimator | 272 KB    | ##################################### | 100% 
tensorflow-2.0.0     | 3 KB      | ##################################### | 100% 
gast-0.2.2           | 138 KB    | ##################################### | 100% 
keras-applications-1 | 33 KB     | ##################################### | 100% 
astor-0.8.0          | 45 KB     | ##################################### | 100% 
opt_einsum-3.1.0     | 54 KB     | ##################################### | 100% 
Preparing transaction: done


# Train the Model

This single line of joeynmt runs the training using the config we made above

In [ ]:
# Train the model
# You can press Ctrl-C to stop. And then run the next cell to save your checkpoints! 
!cd joeynmt; python3 -m joeynmt train configs/transformer_$src$tgt.yaml

2020-02-12 15:55:50,862 Hello! This is Joey-NMT.
2020-02-12 15:55:52,201 Total params: 12152320
2020-02-12 15:55:52,202 Trainable parameters: ['decoder.layer_norm.bias', 'decoder.layer_norm.weight', 'decoder.layers.0.dec_layer_norm.bias', 'decoder.layers.0.dec_layer_norm.weight', 'decoder.layers.0.feed_forward.layer_norm.bias', 'decoder.layers.0.feed_forward.layer_norm.weight', 'decoder.layers.0.feed_forward.pwff_layer.0.bias', 'decoder.layers.0.feed_forward.pwff_layer.0.weight', 'decoder.layers.0.feed_forward.pwff_layer.3.bias', 'decoder.layers.0.feed_forward.pwff_layer.3.weight', 'decoder.layers.0.src_trg_att.k_layer.bias', 'decoder.layers.0.src_trg_att.k_layer.weight', 'decoder.layers.0.src_trg_att.output_layer.bias', 'decoder.layers.0.src_trg_att.output_layer.weight', 'decoder.layers.0.src_trg_att.q_layer.bias', 'decoder.layers.0.src_trg_att.q_layer.weight', 'decoder.layers.0.src_trg_att.v_layer.bias', 'decoder.layers.0.src_trg_att.v_layer.weight', 'decoder.layers.0.trg_trg_att.k_l

2020-02-12 15:55:55,584 cfg.name                           : entiv_transformer
2020-02-12 15:55:55,584 cfg.data.src                       : en
2020-02-12 15:55:55,584 cfg.data.trg                       : tiv
2020-02-12 15:55:55,584 cfg.data.train                     : data/entiv/train.bpe
2020-02-12 15:55:55,585 cfg.data.dev                       : data/entiv/dev.bpe
2020-02-12 15:55:55,585 cfg.data.test                      : data/entiv/test.bpe
2020-02-12 15:55:55,585 cfg.data.level                     : bpe
2020-02-12 15:55:55,585 cfg.data.lowercase                 : False
2020-02-12 15:55:55,585 cfg.data.max_sent_length           : 100
2020-02-12 15:55:55,585 cfg.data.src_vocab                 : data/entiv/vocab.txt
2020-02-12 15:55:55,585 cfg.data.trg_vocab                 : data/entiv/vocab.txt
2020-02-12 15:55:55,585 cfg.testing.beam_size              : 5
2020-02-12 15:55:55,585 cfg.testing.alpha                  : 1.0
2020-02-12 15:55:55,585 cfg.training.random_seed           :

2020-02-12 15:58:09,004 Epoch   1 Step:     1100 Batch Loss:     3.681341 Tokens per Sec:    21252, Lr: 0.000300
2020-02-12 15:58:19,066 Epoch   1 Step:     1200 Batch Loss:     3.286341 Tokens per Sec:    22182, Lr: 0.000300
2020-02-12 15:58:29,003 Epoch   1 Step:     1300 Batch Loss:     3.167710 Tokens per Sec:    22510, Lr: 0.000300
2020-02-12 15:58:38,931 Epoch   1 Step:     1400 Batch Loss:     3.563505 Tokens per Sec:    22049, Lr: 0.000300
2020-02-12 15:58:48,935 Epoch   1 Step:     1500 Batch Loss:     3.639344 Tokens per Sec:    22684, Lr: 0.000300
2020-02-12 15:58:58,889 Epoch   1 Step:     1600 Batch Loss:     3.228676 Tokens per Sec:    22208, Lr: 0.000300
2020-02-12 15:59:08,764 Epoch   1 Step:     1700 Batch Loss:     3.194575 Tokens per Sec:    21941, Lr: 0.000300
2020-02-12 15:59:18,664 Epoch   1 Step:     1800 Batch Loss:     3.024248 Tokens per Sec:    22794, Lr: 0.000300
2020-02-12 15:59:28,757 Epoch   1 Step:     1900 Batch Loss:     3.275215 Tokens per Sec:    211

2020-02-12 16:04:19,315 Epoch   2 Step:     4100 Batch Loss:     2.247452 Tokens per Sec:    22159, Lr: 0.000300
2020-02-12 16:04:29,221 Epoch   2 Step:     4200 Batch Loss:     2.779771 Tokens per Sec:    22260, Lr: 0.000300
2020-02-12 16:04:39,354 Epoch   2 Step:     4300 Batch Loss:     2.120739 Tokens per Sec:    21882, Lr: 0.000300
2020-02-12 16:04:49,391 Epoch   2 Step:     4400 Batch Loss:     2.848859 Tokens per Sec:    21879, Lr: 0.000300
2020-02-12 16:04:59,376 Epoch   2 Step:     4500 Batch Loss:     2.804246 Tokens per Sec:    22455, Lr: 0.000300
2020-02-12 16:05:09,519 Epoch   2 Step:     4600 Batch Loss:     2.565914 Tokens per Sec:    21965, Lr: 0.000300
2020-02-12 16:05:19,682 Epoch   2 Step:     4700 Batch Loss:     2.769480 Tokens per Sec:    21692, Lr: 0.000300
2020-02-12 16:05:29,775 Epoch   2 Step:     4800 Batch Loss:     2.822880 Tokens per Sec:    21512, Lr: 0.000300
2020-02-12 16:05:39,817 Epoch   2 Step:     4900 Batch Loss:     2.971874 Tokens per Sec:    217

2020-02-12 16:10:23,420 Epoch   3 Step:     7100 Batch Loss:     2.392289 Tokens per Sec:    22390, Lr: 0.000300
2020-02-12 16:10:33,255 Epoch   3 Step:     7200 Batch Loss:     2.308585 Tokens per Sec:    22352, Lr: 0.000300
2020-02-12 16:10:43,111 Epoch   3 Step:     7300 Batch Loss:     2.353991 Tokens per Sec:    22982, Lr: 0.000300
2020-02-12 16:10:51,099 Epoch   3: total training loss 6184.23
2020-02-12 16:10:51,099 EPOCH 4
2020-02-12 16:10:53,407 Epoch   4 Step:     7400 Batch Loss:     2.594020 Tokens per Sec:    18604, Lr: 0.000300
2020-02-12 16:11:03,264 Epoch   4 Step:     7500 Batch Loss:     2.548170 Tokens per Sec:    22402, Lr: 0.000300
2020-02-12 16:11:13,196 Epoch   4 Step:     7600 Batch Loss:     2.366792 Tokens per Sec:    22935, Lr: 0.000300
2020-02-12 16:11:23,085 Epoch   4 Step:     7700 Batch Loss:     2.471555 Tokens per Sec:    22248, Lr: 0.000300
2020-02-12 16:11:32,991 Epoch   4 Step:     7800 Batch Loss:     2.077398 Tokens per Sec:    22014, Lr: 0.000300
2

...

2020-02-12 21:22:21,448 Epoch  67 Step:   164100 Batch Loss:     1.479446 Tokens per Sec:    22097, Lr: 0.000300
2020-02-12 21:22:31,338 Epoch  67 Step:   164200 Batch Loss:     1.453567 Tokens per Sec:    22385, Lr: 0.000300
2020-02-12 21:22:41,451 Epoch  67 Step:   164300 Batch Loss:     1.358651 Tokens per Sec:    21795, Lr: 0.000300
2020-02-12 21:22:51,718 Epoch  67 Step:   164400 Batch Loss:     1.157368 Tokens per Sec:    21548, Lr: 0.000300
2020-02-12 21:23:01,888 Epoch  67 Step:   164500 Batch Loss:     1.052091 Tokens per Sec:    21355, Lr: 0.000300
2020-02-12 21:23:11,869 Epoch  67 Step:   164600 Batch Loss:     1.465715 Tokens per Sec:    22545, Lr: 0.000300
2020-02-12 21:23:21,879 Epoch  67 Step:   164700 Batch Loss:     1.388363 Tokens per Sec:    21592, Lr: 0.000300
2020-02-12 21:23:24,985 Epoch  67: total training loss 3381.95
2020-02-12 21:23:24,985 EPOCH 68
2020-02-12 21:23:32,104 Epoch  68 Step:   164800 Batch Loss:     1.100460 Tokens per Sec:    21014, Lr: 0.000300


2020-02-12 21:28:19,756 Epoch  68 Step:   167100 Batch Loss:     1.320471 Tokens per Sec:    22520, Lr: 0.000300
2020-02-12 21:28:28,596 Epoch  68: total training loss 3378.79
2020-02-12 21:28:28,597 EPOCH 69
2020-02-12 21:28:29,860 Epoch  69 Step:   167200 Batch Loss:     1.252517 Tokens per Sec:    19149, Lr: 0.000300
2020-02-12 21:28:39,683 Epoch  69 Step:   167300 Batch Loss:     0.909732 Tokens per Sec:    22025, Lr: 0.000300
2020-02-12 21:28:49,603 Epoch  69 Step:   167400 Batch Loss:     1.272224 Tokens per Sec:    21858, Lr: 0.000300
2020-02-12 21:28:59,517 Epoch  69 Step:   167500 Batch Loss:     1.142943 Tokens per Sec:    21971, Lr: 0.000300
2020-02-12 21:29:09,505 Epoch  69 Step:   167600 Batch Loss:     1.449285 Tokens per Sec:    22401, Lr: 0.000300
2020-02-12 21:29:19,519 Epoch  69 Step:   167700 Batch Loss:     1.524561 Tokens per Sec:    21455, Lr: 0.000300
2020-02-12 21:29:29,495 Epoch  69 Step:   167800 Batch Loss:     1.219512 Tokens per Sec:    22015, Lr: 0.000300


2020-02-12 21:34:16,872 Epoch  70 Step:   170100 Batch Loss:     1.500207 Tokens per Sec:    21710, Lr: 0.000210
2020-02-12 21:34:26,790 Epoch  70 Step:   170200 Batch Loss:     1.456264 Tokens per Sec:    22478, Lr: 0.000210
2020-02-12 21:34:36,775 Epoch  70 Step:   170300 Batch Loss:     1.225434 Tokens per Sec:    22160, Lr: 0.000210
2020-02-12 21:34:46,674 Epoch  70 Step:   170400 Batch Loss:     1.147439 Tokens per Sec:    22633, Lr: 0.000210
2020-02-12 21:34:56,574 Epoch  70 Step:   170500 Batch Loss:     1.492128 Tokens per Sec:    21642, Lr: 0.000210
2020-02-12 21:35:06,698 Epoch  70 Step:   170600 Batch Loss:     1.142891 Tokens per Sec:    21335, Lr: 0.000210
2020-02-12 21:35:16,806 Epoch  70 Step:   170700 Batch Loss:     1.164842 Tokens per Sec:    21830, Lr: 0.000210
2020-02-12 21:35:26,878 Epoch  70 Step:   170800 Batch Loss:     1.104715 Tokens per Sec:    22225, Lr: 0.000210
2020-02-12 21:35:37,001 Epoch  70 Step:   170900 Batch Loss:     1.374452 Tokens per Sec:    214

2020-02-12 21:40:12,345 Epoch  71 Step:   173100 Batch Loss:     1.539012 Tokens per Sec:    21999, Lr: 0.000210
2020-02-12 21:40:22,200 Epoch  71 Step:   173200 Batch Loss:     1.469249 Tokens per Sec:    22888, Lr: 0.000210
2020-02-12 21:40:32,063 Epoch  71 Step:   173300 Batch Loss:     1.316316 Tokens per Sec:    22537, Lr: 0.000210
2020-02-12 21:40:41,952 Epoch  71 Step:   173400 Batch Loss:     1.058633 Tokens per Sec:    21707, Lr: 0.000210
2020-02-12 21:40:51,943 Epoch  71 Step:   173500 Batch Loss:     1.452735 Tokens per Sec:    22243, Lr: 0.000210
2020-02-12 21:41:01,866 Epoch  71 Step:   173600 Batch Loss:     1.478271 Tokens per Sec:    22119, Lr: 0.000210
2020-02-12 21:41:11,714 Epoch  71 Step:   173700 Batch Loss:     1.305297 Tokens per Sec:    21938, Lr: 0.000210
2020-02-12 21:41:21,573 Epoch  71 Step:   173800 Batch Loss:     1.453498 Tokens per Sec:    22531, Lr: 0.000210
2020-02-12 21:41:31,473 Epoch  71 Step:   173900 Batch Loss:     1.310819 Tokens per Sec:    222

2020-02-12 21:46:10,788 Epoch  72 Step:   176100 Batch Loss:     1.370144 Tokens per Sec:    21528, Lr: 0.000210
2020-02-12 21:46:20,968 Epoch  72 Step:   176200 Batch Loss:     1.523032 Tokens per Sec:    21737, Lr: 0.000210
2020-02-12 21:46:31,047 Epoch  72 Step:   176300 Batch Loss:     1.417220 Tokens per Sec:    22094, Lr: 0.000210


In [21]:
!mkdir -p "$experiment_path/models/${src}${tgt}_transformer/"

In [22]:
# Copy the created models from the notebook storage to google drive for persistant storage 
!cp -r joeynmt/models/${src}${tgt}_transformer/* "$experiment_path/models/${src}${tgt}_transformer/"

In [23]:
# Output our validation accuracy
! cat "$experiment_path/models/${src}${tgt}_transformer/validations.txt"

Steps: 1000	Loss: 105431.41406	PPL: 35.21214	bleu: 2.23576	LR: 0.00030000	*
Steps: 2000	Loss: 90648.33594	PPL: 21.37090	bleu: 3.87765	LR: 0.00030000	*
Steps: 3000	Loss: 83058.23438	PPL: 16.53769	bleu: 4.98396	LR: 0.00030000	*
Steps: 4000	Loss: 77589.78125	PPL: 13.74840	bleu: 7.26332	LR: 0.00030000	*
Steps: 5000	Loss: 73523.78906	PPL: 11.98404	bleu: 9.31015	LR: 0.00030000	*
Steps: 6000	Loss: 70898.39062	PPL: 10.96702	bleu: 10.50791	LR: 0.00030000	*
Steps: 7000	Loss: 68224.22656	PPL: 10.01978	bleu: 11.86918	LR: 0.00030000	*
Steps: 8000	Loss: 66128.57031	PPL: 9.33501	bleu: 13.12602	LR: 0.00030000	*
Steps: 9000	Loss: 64338.49219	PPL: 8.78727	bleu: 14.40652	LR: 0.00030000	*
Steps: 10000	Loss: 62378.29688	PPL: 8.22428	bleu: 15.51252	LR: 0.00030000	*
Steps: 11000	Loss: 61080.13672	PPL: 7.87143	bleu: 15.65950	LR: 0.00030000	*
Steps: 12000	Loss: 59583.07812	PPL: 7.48327	bleu: 16.62673	LR: 0.00030000	*
Steps: 13000	Loss: 58631.89453	PPL: 7.24665	bleu: 16.84451	LR: 0.00030000	*
Steps: 14000	Loss:

In [25]:
# Test our model
! cd joeynmt; python3 -m joeynmt test configs/transformer_$src$tgt.yaml

2020-02-13 08:07:47,711 Hello! This is Joey-NMT.
2020-02-13 08:08:17,568  dev bleu:  30.29 [Beam search decoding with beam size = 5 and alpha = 1.0]
2020-02-13 08:08:23,920 test bleu:  44.70 [Beam search decoding with beam size = 5 and alpha = 1.0]
